In [13]:
import face_recognition
import cv2
from sklearn.cluster import DBSCAN
import numpy as np
import os
import pickle
import signal
import sys
import math
import time
import random
from matplotlib import pyplot as plt
%matplotlib inline
from bokeh.plotting import figure
from bokeh.io import output_notebook, show, push_notebook
from imutils import paths


In [14]:

output_notebook()


def imshow(tit, image) :
    plt.title(tit)    
    if len(image.shape) == 3 :
        plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    else :
        plt.imshow(image, cmap="gray")
    plt.show()
    
    
def create_win(frames, scale=1.0) :    
    global myImage
    
    all = []
    for f in frames :
        if len(f.shape ) !=  3 : f = cv2.cvtColor(f, cv2.COLOR_GRAY2BGR)
        all.append(f)
    frame = np.vstack(all)
    
    fr=cv2.cvtColor(frame, cv2.COLOR_BGR2RGBA) # because Bokeh expects a RGBA image
    fr=cv2.flip(fr, -1) # because Bokeh flips vertically
    width=fr.shape[1]
    height=fr.shape[0]    

    p = figure(x_range=(0,width), y_range=(0,height), output_backend="webgl", width=int(width*scale), height=int(height*scale))    
    myImage = p.image_rgba(image=[fr], x=0, y=0, dw=width, dh=height)
    show(p, notebook_handle=True)   
    
    
def update_win(frames) :
    
    all = []
    for f in frames :
        if len(f.shape ) !=  3 : f = cv2.cvtColor(f, cv2.COLOR_GRAY2BGR)
        all.append(f)
    frame = np.vstack(all)
    
    fr=cv2.cvtColor(frame, cv2.COLOR_BGR2RGBA)
    fr=cv2.flip(fr, -1)
    myImage.data_source.data['image']=[fr]
    push_notebook()


Loading BokehJS ...

In [15]:
src = cv2.VideoCapture('C:/Users/82107/Desktop/TIL/til/simple_project/face/music.mp4')
faces = []
frame_id = 0
frame_rate = src.get(5)
stop_at_frame = int(0 * frame_rate)
print("start encoding from src: %dx%d, %f frame/sec" % (src.get(3), src.get(4), frame_rate))


start encoding from src: 1280x720, 29.970030 frame/sec


In [16]:
imagePaths = list(paths.list_images("./knowns"))
 
knownEncodings = []
knownNames = []

for (i, imagePath) in enumerate(imagePaths):    
    name = imagePath.split(os.path.sep)[-2]  #뒤쪽2자리빼기
    print(f"{name}   -   {imagePath}") 
    image = cv2.imread(imagePath)
    boxes = face_recognition.face_locations(image)
    encodings = face_recognition.face_encodings(image, boxes) 

    for encoding in encodings:        
        knownEncodings.append(encoding)
        knownNames.append(name)
        
import pickle
data = {"encodings": knownEncodings, "names": knownNames} #둘 다 리스트
f = open("known.bin", "wb")  #binary 통채로 저장,불러들이는 방식
f.write(pickle.dumps(data))
f.close()

./knowns   -   ./knowns\lee.jpg
./knowns   -   ./knowns\McYou.jpg
./knowns   -   ./knowns\rain.jpg
lee   -   ./knowns\lee\1.jpg
lee   -   ./knowns\lee\10.jpg
lee   -   ./knowns\lee\2.jpg
lee   -   ./knowns\lee\3.jpg
lee   -   ./knowns\lee\4.jpg
lee   -   ./knowns\lee\5.jpg
lee   -   ./knowns\lee\6.jpg
lee   -   ./knowns\lee\7.jpg
lee   -   ./knowns\lee\8.jpg
lee   -   ./knowns\lee\9.jpg
McYou   -   ./knowns\McYou\1.jpg
McYou   -   ./knowns\McYou\10.jpg
McYou   -   ./knowns\McYou\2.jpg
McYou   -   ./knowns\McYou\3.jpg
McYou   -   ./knowns\McYou\4.jpg
McYou   -   ./knowns\McYou\5.jpg
McYou   -   ./knowns\McYou\6.jpg
McYou   -   ./knowns\McYou\7.jpg
McYou   -   ./knowns\McYou\8.jpg
McYou   -   ./knowns\McYou\9.jpg
rain   -   ./knowns\rain\1.jpg
rain   -   ./knowns\rain\10.jpg
rain   -   ./knowns\rain\2.jpg
rain   -   ./knowns\rain\3.jpg
rain   -   ./knowns\rain\4.jpg
rain   -   ./knowns\rain\5.jpg
rain   -   ./knowns\rain\6.jpg
rain   -   ./knowns\rain\7.jpg
rain   -   ./knowns\rain\8.jpg

In [19]:
data = pickle.loads(open("known.bin", "rb").read())
for i in range(100):
    
    ret, frame = src.read()
    if i==0:
        create_win([frame], scale=0.5) 
    if not ret:
        break
        
    image = frame[:, :, ::-1]
    
    boxes = face_recognition.face_locations(image,model="hog")
    encodings = face_recognition.face_encodings(image, boxes)

    names = []
    for encoding in encodings:
        matches = face_recognition.compare_faces(data["encodings"], encoding)
        name = "Unknown"
        if True in matches:  #리스트 안에서 하나라도 특정 값(true)이 있으면
            matchedIdxs = [i for (i, b) in enumerate(matches) if b]
            counts = {} 
            for i in matchedIdxs:
                name = data["names"][i]
                counts[name] = counts.get(name, 0) + 1  #name에 해당하는 element 불러오고 없으면 0 반환
            name = max(counts, key=counts.get)
        names.append(name)
    for ((top, right, bottom, left), name) in zip(boxes, names):
        top *= 4
        right *= 4
        bottom *= 4
        left *= 4

        # Draw a box around the face
        cv2.rectangle(frame, (left, top), (right, bottom), (0, 0, 255), 2)

        # Draw a label with a name below the face
        cv2.rectangle(frame, (left, bottom - 35), (right, bottom), (0, 0, 255), cv2.FILLED)
        font = cv2.FONT_HERSHEY_DUPLEX
        cv2.putText(frame, name, (left + 6, bottom - 6), font, 1.0, (255, 255, 255), 1)

    
    update_win([frame])

